<a href="https://colab.research.google.com/github/albachiarabellaroba/HW3---Group-16/blob/main/Copia_di_main_Albachiara.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

#**Homework 3 - Places of the world**

*Authors: Bellaroba Albachiara, Mazza Ludovica*

To get started, let's import all the libraries we will need.

In [1]:
from bs4 import BeautifulSoup
import bs4
import requests
import os.path
import lxml
import re
import codecs
import csv
import nltk
from datetime import datetime
from tqdm import tqdm
import time
import pandas as pd

In order to work in a faster environment, we link our work to a shared drive folder.

In [2]:
from google.colab import drive
drive.mount('/content/drive/') 

Mounted at /content/drive/


## 1. Data collection

### 1.1. Get the list of places

At this point we're creating a text file with all the link related to the 7200 places we will analyze.

In [ ]:
linklist = open('/content/drive/MyDrive/ADM_HW3/linklist.txt', 'w')

for i in tqdm(range(1, 401)):
    link = f'https://www.atlasobscura.com/places?page={i}&sort=likes_count'
    cont = requests.get(link)
    soup = BeautifulSoup(cont.content, features='lxml')
    for a in soup.find_all('a', class_='content-card content-card-place'):
        linklist.write(a.get('href')+'\n')
        
linklist.close()

100%|██████████| 400/400 [02:05<00:00,  3.18it/s]


Control that we have all the link.

In [ ]:
file = open('/content/drive/MyDrive/ADM_HW3/linklist.txt', 'r')
count=0
for i in file:
  if i != '\n':
    count += 1
file.close
print(count)

7200


### 1.2. Crawl places

In [ ]:
def download(start, finish):
    header = {'User-Agent': 'Mozilla/5.0 (Macintosh; Intel Mac OS X 10_10_1) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/39.0.2171.95 Safari/537.36'}
    for i in tqdm(range(start, finish)):
      cart = '/content/drive/MyDrive/ADM_HW3/Html_page/page_{}'.format(i)
      os.makedirs(cart)
      
      f = open('/content/drive/MyDrive/ADM_HW3/linklist.txt', 'r', encoding='utf8')
      l = f.readlines()[(i-1)*18:(i)*18]
      l = [k.rstrip() for k in l]
      f.close

      m = 1+18*(i-1)

      for link in l:
        link = 'https://www.atlasobscura.com' + link
        html = requests.get(link, headers = header)
        if html.status_code != 200:
          time.sleep(200)
          html = requests.get(link, headers = header)


        name = '{}/{}.html'.format(cart, m)
        text = open(name, 'w', encoding='utf8')
        text.write(html.text)
        text.close
        m=m+1


In [ ]:
download(1, 401)

100%|██████████| 100/100 [26:07<00:00, 15.67s/it]


### 1.3 Parse downloaded pages

In [ ]:
placeName=[]
placeTags=[]
numPeopleVisited=[]
numPeopleWant=[]
placeDesc=[]
placeShortDesc=[]
placeNearby=[]
placeAddress=[]
placeAlt=[]
placeLong=[]
placeEditors=[]
placePubDate=[]
placeRelatedLists=[]
placeRelatedPlaces=[]
placeURL=[]

In [ ]:

 for i in tqdm(range(1,401)):
   files = os.listdir('/content/drive/MyDrive/ADM_HW3/Html_page/page_'+str(i))
   for k in range(((18*(int(i)-1))+1), (18*int(i)+1)):
     file = open('/content/drive/MyDrive/ADM_HW3/Html_page/page_'+str(i)+'/'+str(k)+'.html', 'r', encoding='utf8')
     soup=bs4.BeautifulSoup(file, 'lxml')

     try:
       name=soup.find('h1', {'class':'DDPage__header-title'}).text
       placeName.append(name)
     except:
       placeName.append('')
         
     try:
       tag=soup.find_all('a', {'class':'itemTags__link js-item-tags-link'})
       tag=[i.get('href').split('/categories/')[1] for i in tag]
       placeTags.append(tag)
     except:
       placeTags.append('')
       
     try:
       visitors=soup.find_all('div', {'class':'title-md item-action-count'})[0].text.strip()
       numPeopleVisited.append(visitors)
     except:
       numPeopleVisited.append('')
    
     try:
       want=soup.find_all('div', {'class':'title-md item-action-count'})[1].text.strip()
       numPeopleWant.append(want)
     except:
       numPeopleWant.append('')

     try:
       desc=soup.find('div', {'class':'DDP__body-copy'}).text.strip()
       placeDesc.append(desc)
     except:
       placeDesc.append('')

     try:
       shdesc=soup.find('h3', {'class':'DDPage__header-dek'}).text.strip()
       placeShortDesc.append(shdesc)
     except:
       placeShortDesc.append('')

     try:
       nearby=soup.find_all('div', {'class':'DDPageSiderailRecirc__item-title'})
       nearby=[i.get_text() for i in nearby]
       placeNearby.append(nearby)
     except:
       placeNearby.append('')

     try:
       address=soup.find_all('address', {'class':'DDPageSiderail__address'})[0]
       address=address.find('div').get_text(separator=' ').split('\n')[0]
       placeAddress.append(address)
     except:
       placeAddress.append('')

     try:
       coordinates=soup.find_all('div', {'class':'DDPageSiderail__coordinates js-copy-coordinates'})[0].text.strip()
       p=coordinates.split(', ')
       placeAlt.append(p[0])
       placeLong.append(p[1])
     except:
       placeAlt.append('')
       placeLong.append('')

     try:
       editors=soup.find_all('div', {'class':'ugc-editor-icons'})
       editors=[i.findChildren('a')[0].get('href') for i in editors]
       editors=[k.split('/users/')[1] for k in editors]
       placeEditors.append(editors)
     except:
       placeEditors.append('')

     try:
       date=soup.find('div', {'class':'DDPContributor__name'}).text.strip()
       placePubDate.append(date)
     except:
       placePubDate.append('')

     try:
       rellist=soup.find_all('div', {'data-gtm-template':'DDP Footer Recirc Lists'})[0]
       rellist=[i.text.strip() for i in rellist.find_all('h3')]
       placeRelatedLists.append(rellist)
     except:
       placeRelatedLists.append('')

     try:
       relplaces=soup.find_all('div', {'class':'CardRecircSection__title'})
       relplaces=[i for i in relplaces if i.text == 'Related Places'][0]
       relplaces=relplaces.find_all_next('div', {'class':'Card__action-btns vue-js-been-there-everywhere-place'})
       relplaces=[k.get('data-place-title') for k in relplaces]
       placeRelatedPlaces.append(relplaces)
     except:
       placeRelatedPlaces.append('')

     try:
       url=soup.find('meta', attrs={'property':'og:url'})['content']
       placeURL.append(url)
     except:
       placeURL.append('')




100%|██████████| 400/400 [48:41<00:00,  7.30s/it]


In [ ]:
features=pd.DataFrame(columns=['placeName', 'placeTags', 'numPeopleVisited', 'numPeopleWant', 'placeDesc', 'placeShortDesc',
                                            'placeNearby', 'placeAddress', 'placeAlt', 'placeLong', 'placeEditors', 'placePubDate', 
                                            'placeRelatedLists', 'placeRelatedPlaces', 'placeURL'], index=[1,7200])

for i in tqdm(range(0, 7200)):
  features.at[i, 'placeName'] = placeName[i]
  features.at[i, 'placeTags'] = placeTags[i]
  features.at[i, 'numPeopleVisited']= numPeopleVisited[i]
  features.at[i, 'numPeopleWant']= numPeopleWant[i]
  features.at[i, 'placeDesc']= placeDesc[i]
  features.at[i, 'placeShortDesc']= placeShortDesc[i]
  features.at[i, 'placeNearby']= placeNearby[i]
  features.at[i, 'placeAddress']= placeAddress[i]
  features.at[i, 'placeAlt']= placeAlt[i]
  features.at[i, 'placeLong']= placeLong[i]
  features.at[i, 'placeEditors']= placeEditors[i]
  features.at[i, 'placePubDate']= placePubDate[i]
  features.at[i, 'placeRelatedLists']= placeRelatedLists[i]
  features.at[i, 'placeRelatedPlaces']= placeRelatedPlaces[i]
  features.at[i, 'placeURL']= placeURL[i]
  

100%|██████████| 7200/7200 [00:23<00:00, 303.84it/s]


In [ ]:
#os.makedirs('/content/drive/MyDrive/ADM_HW3/tsv_files')
placesfeatures = features.to_csv('/content/drive/MyDrive/ADM_HW3/features.tsv', sep='\t', index=False)

In [39]:
visual=pd.read_csv('/content/drive/MyDrive/ADM_HW3/features.tsv', sep='\t')
visual = visual.drop(labels=[1], axis=0)
visual.head(10)

placeName  \
0                    Highgate Cemetery   
2                    City Hall Station   
3                    Leadenhall Market   
4                       The Wave Organ   
5                  Catacombes de Paris   
6                  The Evolution Store   
7       Magowan's Infinite Mirror Maze   
8   Underground Tunnels of Los Angeles   
9               Secret Tiled Staircase   
10                         Dream House   

                                            placeTags  numPeopleVisited  \
0   ['rivals-week', 'vampires', 'hoaxes', 'occult'...            2625.0   
2   ['subways', 'subterranean', 'infrastructure', ...            1834.0   
3               ['markets', 'film-locations', 'film']            3142.0   
4   ['sea-organ', 'aletrail', 'sounds', 'music', '...            2430.0   
5   ['ossuaries', 'memento-mori', 'catacombs-and-c...            4456.0   
6   ['wonder-cabinets', 'purveyors-of-curiosities'...            2198.0   
7   ['optical-illusions', 'labyrinths', 'optical-o...             909.0   
8   ['tunnels', 'subterranean-sites', 'architectur...             660.0   
9   ['stairs', 'outsider-art', 'architectural-oddi...            2009.0   
10  ['optical-oddities', 'eccentric-homes', 'music...             765.0   

    numPeopleWant                                          placeDesc  \
0          8208.0  Opened in 1839, Highgate is one of London’s mo...   
2          8606.0  The first New York City subway was built and o...   
3          7595.0  The ornate 19th-century painted roof and cobbl...   
4          7425.0  Located on a jetty in the San Francisco Bay, t...   
5          7057.0  In 2004, Parisian police were assigned to do a...   
6          6951.0  Evolution stands out among the clothing stores...   
7          6507.0  People stumble about the labyrinth, arms outst...   
8          6440.0  While the rest of the country was forced to go...   
9          6313.0  The 16th Avenue Staircase is 163 steps of mosa...   
10         6007.0  When walking down Church Street in Tribeca, ke...   

                                       placeShortDesc  \
0   London's creepiest cemetery was once the site ...   
2   A beautiful and abandoned New York subway stat...   
3   This ornate Victorian marketplace was the sett...   
4      A huge musical instrument played by the ocean.   
5   The vast, legendary catacombs hold secrets muc...   
6   A terrific purveyor of natural history objects...   
7   A psychedelic labyrinth on the San Francisco bay.   
8   During prohibition, corrupt city officials ran...   
9   An artsy hidden staircase leads to breathtakin...   
10  La Monte Young and Marian Zazeela's "Dream Hou...   

                                          placeNearby  \
0   ["World's Largest Potted Plant", 'Dick Whittin...   
2   ['African Burial Ground National Monument', 'T...   
3   ['The Cornhill Devils ', "London's Original an...   
4   ['Long Now Orrery', 'The Stern of the Briganti...   
5   ['Sculptures de Décure', 'Arago Medallions', "...   
6   ["Merchant's House Museum", 'The Brown Buildin...   
7   ['Musée Mécanique', 'Jack Early Park', "Fior D...   
8   ['Cathedral of Our Lady of the Angels', 'Trifo...   
9   ['Helen Crocker Russell Library of Horticultur...   
10  ['Aretha Franklin Subway Tributes', 'Farm.One'...   

                                         placeAddress  placeAlt  placeLong  \
0   Swain's Lane, Highgate London, England, N6 Uni...   51.5675    -0.1483   
2   31 Centre St New York, New York, 10007 United ...   40.7134   -74.0046   
3                London, England, EC3V United Kingdom   51.5126    -0.0834   
4   83 Marina Green Dr San Francisco, California, ...   37.8085  -122.4401   
5       1 Place Denfert-Rochereau Paris, 75014 France   48.8343     2.3322   
6   687 Broadway New York, New York, 10012 United ...   40.7281   -73.9948   
7    Pier 39, Building O-11 San Francisco, Califor...   37.8100  -122.4104   
8   320 W Temple St Los Angeles, California, 90012...   34.0558  -1

In [ ]:
#come salvare file tsv

#with open(f'./all_Pages/{i}/{k}', encoding='utf8') as fp:
  #csv.writer(fp, delimiter = "\t").writerow([placeTag, placeName....])

## 2. Search Engine

In [3]:
from nltk.corpus import stopwords
from nltk.stem import PorterStemmer
from nltk.tokenize import RegexpTokenizer
from nltk.tokenize import word_tokenize
import string

nltk.download('stopwords')
nltk.download('punkt')

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Unzipping corpora/stopwords.zip.
[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.


True

Let's define a function that allows us to clean our descriptions

In [4]:
def clean(line):
  #split into token
  tokens = word_tokenize(line)
  #convert to lowercase
  tokens = [w.lower() for w in tokens]
  #remove punctuation
  table = str.maketrans('', '', string.punctuation)
  stripped = [w.translate(table) for w in tokens]
  # remove remaining tokens that are not alphabetic
  words = [word for word in stripped if word.isalnum()]
  #filterout stopwords
  stop_words = set(stopwords.words('english'))
  words = [w for w in words if not w in stop_words]
  #stemming
  ps = PorterStemmer()
  stem_sentence=[]

  for word in words:
    stem_sentence.append(ps.stem(word))

  return stem_sentence

Now to make things easier let's isolate the column we want to work on: DESCRIPTIONS

In [5]:
desc_col=pd.read_csv('/content/drive/MyDrive/ADM_HW3/features.tsv', usecols=['placeDesc'] ,sep='\t')

In [ ]:
def vocabulary(visual):
    dic = {}
    contatore = 1
    for desc in tqdm(visual["placeDesc"]):
        #Cleaning the data
        desc = clean(str(desc))
        for word in desc:
            if word not in dic.keys():
              dic[word]=contatore
              contatore+=1
    return dic

In [44]:
dic1 = vocabulary(visual)
print(len(dic1))

100%|██████████| 7200/7200 [00:52<00:00, 136.28it/s]


### 2.1.1 Create your index!

We have already created the vocabulary file as a dictionary in the last point of the exercise, now we need to invert the index and match the words in the dict with the words in the place's description.

In [77]:
import json
path='/content/drive/MyDrive/ADM_HW3'
with open (path+'vocabulary.json', 'w',encoding = 'utf-8') as j:
    j.write(json.dumps(dic1))

In [78]:
list_clean_words=[]

for i in visual.placeDesc:
  clean_words=clean(str(i))
  list_clean_words.append(clean_words)

[['locat',
  'jetti',
  'san',
  'francisco',
  'bay',
  'wave',
  'organ',
  'built',
  '1986',
  'collabor',
  'exploratorium',
  'artist',
  'peter',
  'richard',
  'built',
  'acoust',
  'sculptur',
  'amplifi',
  'sound',
  'wave',
  'bay',
  'organ',
  'jetti',
  'construct',
  'carv',
  'granit',
  'marbl',
  'demolish',
  'cemeteri',
  'magnific',
  'old',
  'fine',
  'work',
  'piec',
  'form',
  'irregular',
  'terrac',
  'seat',
  'even',
  'trash',
  'holder',
  'instrument',
  'compris',
  '20',
  'pvc',
  'concret',
  'pipe',
  'extend',
  'water',
  'variou',
  'elev',
  'sound',
  'creat',
  'wave',
  'crash',
  'end',
  'pipe',
  'wave',
  'roll',
  'pipe',
  'resound',
  'liquid',
  'music',
  'low',
  'gurgl',
  'note',
  'ebb',
  'flow',
  'restless',
  'movement',
  'ocean',
  'chang',
  'tide',
  'make',
  'music',
  'similar',
  'phenomena',
  'sound',
  'heard',
  'conch',
  'specif',
  'volum',
  'air',
  'reson',
  'specif',
  'frequenc',
  'sort',
  'thing',


In [79]:
visual_copy=visual.copy()
visual_copy["list_clean_words"]=list_clean_words

visual_copy.head(3)

placeName                                          placeTags  \
0  Highgate Cemetery  ['rivals-week', 'vampires', 'hoaxes', 'occult'...   
2  City Hall Station  ['subways', 'subterranean', 'infrastructure', ...   
3  Leadenhall Market              ['markets', 'film-locations', 'film']   

   numPeopleVisited  numPeopleWant  \
0            2625.0         8208.0   
2            1834.0         8606.0   
3            3142.0         7595.0   

                                           placeDesc  \
0  Opened in 1839, Highgate is one of London’s mo...   
2  The first New York City subway was built and o...   
3  The ornate 19th-century painted roof and cobbl...   

                                      placeShortDesc  \
0  London's creepiest cemetery was once the site ...   
2  A beautiful and abandoned New York subway stat...   
3  This ornate Victorian marketplace was the sett...   

                                         placeNearby  \
0  ["World's Largest Potted Plant", 'Dick Whittin...   
2  ['African Burial Ground National Monument', 'T...   
3  ['The Cornhill Devils ', "London's Original an...   

                                        placeAddress  placeAlt  placeLong  \
0  Swain's Lane, Highgate London, England, N6 Uni...   51.5675    -0.1483   
2  31 Centre St New York, New York, 10007 United ...   40.7134   -74.0046   
3               London, England, EC3V United Kingdom   51.5126    -0.0834   

                        placeEditors    placePubDate  \
0                    ['anthonyhogg']  August 9, 2014   
2  ['rebekah-otto', 'annetta-black']     May 8, 2010   
3     ['meghanneal', 'gavin-292130']  August 1, 2016   

                                   placeRelatedLists  \
0  ["The World's Top 100 Wonders in 2018", "Londo...   
2  ['30 Unexpected Places to Have a Joyful Advent...   
3  ['The Ultimate Guide to Stunning, Surprising, ...   

                                  placeRelatedPlaces  \
0  ['Jewett City Vampires', 'Tomb of the Mather F...   
2  ['Crystal Palace Subway', 'Moscow Metro Statio...   
3  ['Rivendell', 'Bagdad Cafe', 'Gare de la Ciota...   

                                            placeURL  \
0  http://www.atlasobscura.com/places/highgate-ce...   
2  http://www.atlasobscura.com/places/city-hall-s...   
3  http://www.atlasobscura.com/places/leadenhall-...   

                                    list_clean_words  
0  [open, 1839, highgat, one, london, infam, ceme...  
2  [first, new, york, citi, subway, built, oper, ...  
3  [ornat, 19thcenturi, paint, roof, cobbl, floor...

In [81]:
inverted_idx = {}

for word, item_id in dic1.items():
    inverted_idx[item_id] = list(visual_copy[visual_copy.list_clean_words.apply(lambda row: word in row)].index)
  

In [82]:
inverted_idx

{1: [0,
  2,
  5,
  7,
  16,
  18,
  19,
  20,
  23,
  25,
  27,
  30,
  32,
  35,
  37,
  42,
  44,
  48,
  49,
  51,
  57,
  59,
  72,
  73,
  74,
  75,
  77,
  80,
  81,
  83,
  89,
  94,
  98,
  99,
  101,
  104,
  105,
  106,
  107,
  108,
  109,
  110,
  120,
  123,
  124,
  125,
  131,
  135,
  137,
  141,
  143,
  144,
  147,
  149,
  150,
  151,
  152,
  153,
  155,
  157,
  160,
  162,
  166,
  171,
  173,
  179,
  182,
  183,
  187,
  190,
  191,
  196,
  197,
  202,
  206,
  209,
  211,
  213,
  220,
  221,
  224,
  228,
  239,
  240,
  241,
  244,
  248,
  250,
  252,
  254,
  256,
  257,
  259,
  260,
  261,
  267,
  268,
  269,
  270,
  271,
  273,
  276,
  286,
  287,
  289,
  291,
  295,
  300,
  301,
  307,
  309,
  312,
  314,
  317,
  318,
  319,
  320,
  329,
  330,
  334,
  342,
  351,
  355,
  356,
  357,
  361,
  364,
  365,
  366,
  367,
  368,
  369,
  370,
  377,
  378,
  379,
  381,
  382,
  386,
  390,
  391,
  392,
  395,
  397,
  399,
  403,
  412,
  419,

In [75]:
dic2={}
contatore=0

for descrizione in visual.placeDesc:
  descrizione=clean(str(descrizione))
  for parola in descrizione:
    if dic1[parola] in dic2.keys():
      print




KeyError: ignored

### 2.1.2 Execute the query

### 2.2 Conjunctive query & Ranking score

### 2.2.1 Inverted index

### 2.2.2 Execute the query

## 3. Define a new score!

## 4. Visualizing the most relevant places

## 5. BONUS: More complex search engine

## 6. Command line question

## 7. Theoretical question